In [1]:
import pandas as pd

sample = pd.read_csv("sample.csv")

## Classification


In [5]:
from sklearn import tree
from sklearn import metrics
from sklearn.grid_search import GridSearchCV
from sklearn.model_selection import train_test_split
import numpy as np


def test_trip_distance_price_feature_dec_tree(sample):
    X = sample[["Tip_amount", 
                "Total_amount",
                "Tolls_amount",
                "improvement_surcharge",
                "Trip_distance"]]
    y = sample["tip_percentage"]
    dec_tree = tree.DecisionTreeRegressor()
    X_train, X_test, y_train, y_test = train_test_split(
        X, y, test_size=0.33)
    dec_tree.fit(X_train, y_train)
    y_pred = dec_tree.predict(X_test)
    print("MSE", metrics.mean_squared_error(y_test, y_pred))
    num_features = len(X)
    print("Fitting with GridSearch")
    param_grid = {"criterion": ["mse", "friedman_mse"],
              "min_samples_split": [2, 10, 20],
              "max_depth": [None, 2, 10, 20],
              "min_samples_leaf": [1, 5, 10],
              "max_leaf_nodes": [None, 5, 10, 20],
              }
    
    dec_tree = tree.DecisionTreeRegressor()
    grid_search = GridSearchCV(dec_tree,
                              param_grid=param_grid,
                              cv=3, scoring="neg_mean_squared_error")
    grid_search.fit(X, y)
    grid_scores = grid_search.grid_scores_
    top_scores = sorted(grid_scores,
                       key=lambda t:t[1],
                        reverse=True)[:3]
    for index, score in enumerate(top_scores):
        print("Model Rank", index+1)
        print("Mean validation Score", score.mean_validation_score)
        print("Std of validation score", np.std(score.cv_validation_scores))
        print("Parameters:", score.parameters)
    print("feature importance")
    feature_importance = grid_search.best_estimator_.feature_importances_
    for index, col in enumerate(X.columns):
        print(col, feature_importance[index])
        
test_trip_distance_price_feature_dec_tree(sample)

MSE 0.45555204325186405
Fitting with GridSearch
Model Rank 1
Mean validation Score -0.7824587185275295
Std of validation score 0.15722681556783957
Parameters: {'criterion': 'friedman_mse', 'max_depth': 20, 'max_leaf_nodes': None, 'min_samples_leaf': 1, 'min_samples_split': 2}
Model Rank 2
Mean validation Score -0.7942518748648246
Std of validation score 0.11336443601311968
Parameters: {'criterion': 'mse', 'max_depth': 20, 'max_leaf_nodes': None, 'min_samples_leaf': 1, 'min_samples_split': 2}
Model Rank 3
Mean validation Score -0.7975921645310559
Std of validation score 0.2292870913008529
Parameters: {'criterion': 'mse', 'max_depth': None, 'max_leaf_nodes': None, 'min_samples_leaf': 1, 'min_samples_split': 2}
feature importance
Tip_amount 0.937063908616152
Total_amount 0.042881903909262734
Tolls_amount 2.1869129472645814e-05
improvement_surcharge 0.0007382614635051287
Trip_distance 0.01929405688160748


In [12]:
import pydotplus 
from IPython.display import Image
from sklearn import ensemble

def test_time_gbc(sample):
    map_values = {
        False: 0,
        True: 1
    }
    y = sample["tip_percentage"] != 0
    y = y.map(map_values)
    X = sample[["Total_amount",
                "Tolls_amount",
                "improvement_surcharge",
                "Trip_distance"]]
    num_features = len(X)
    params = {"criterion": "friedman_mse",
              "min_samples_split": 10, 
              "max_depth": num_features*3,
              "min_samples_leaf": 5,
              "max_leaf_nodes": None,
              "warm_start": True
              }
    X_train, X_test, y_train, y_test = train_test_split(
        X, y, test_size=0.33)
    gbc = ensemble.GradientBoostingClassifier(**params)
    
    gbc.fit(X_train, y_train)
    y_pred_test = gbc.predict(X_test)
    print()
    print("F1:", metrics.classification_report(y_test, y_pred_test))
    print("feature importance:")
    feature_importances = gbc.feature_importances_
    for index, column in enumerate(X.columns):
        print(column, feature_importances[index])
    y_pred_train = gbc.predict(X_train)    
    tree_clf = tree.DecisionTreeClassifier()
    tree_model = tree_clf.fit(X_train, y_pred_train)

    dot_data = tree.export_graphviz(tree_model, out_file=None, 
                             feature_names=X_train.columns,  
                             class_names="tip_percentage",  
                             filled=True, rounded=True,  
                             special_characters=True)  
    graph = pydotplus.graph_from_dot_data(dot_data)  
    picture = Image(graph.create_png())
    return picture
    
picture = test_time_gbc(sample)
picture


F1:              precision    recall  f1-score   support

          0       0.88      0.92      0.90      9773
          1       0.88      0.82      0.85      6727

avg / total       0.88      0.88      0.88     16500

feature importance:
Total_amount 0.42913886043151217
Tolls_amount 0.005756914361542072
improvement_surcharge 0.0067955493877029875
Trip_distance 0.5583086758192428
dot: graph is too large for cairo-renderer bitmaps. Scaling by 0.281719 to fit



In [ ]:
from xgboost.sklearn import XGBRegressor
from sklearn.grid_search import GridSearchCV

def test_distance_time_price_feature_xgbr(sample):
    X = sample[["Tip_amount", 
                "Total_amount",
                "Tolls_amount",
                "improvement_surcharge",
                "Trip_distance"]]
    y = sample["tip_percentage"]
    
    xgb1 = XGBRegressor()
    parameters = {'objective':['reg:linear'],
                  'learning_rate': [.03, 0.05], 
                  'max_depth': [5, 10, 15],
                  'min_child_weight': [5, 10, 15],
                  'silent': [1],
                  'subsample': [0.3, 0.5],
                  'colsample_bytree': [0.3, 0.5],
                  'colsample_bylevel': [0.3, 0.5],
                  'reg_lambda':[0.5, 1, 5],
                  'n_estimators': [50, 100, 500]}

    grid_search = GridSearchCV(xgb1,
                            parameters,
                            cv = 2,
                            n_jobs = 5,
                            verbose=True,
                            scoring="neg_mean_squared_error")

    grid_search.fit(X, y)
    grid_scores = grid_search.grid_scores_
    top_scores = sorted(grid_scores,
                       key=lambda t:t[1],
                        reverse=True)[:3]
    for index, score in enumerate(top_scores):
        print("Model Rank", index+1)
        print("Mean validation Score", score.mean_validation_score)
        print("Std of validation score", np.std(score.cv_validation_scores))
        print("Parameters:", score.parameters)

test_distance_time_price_feature_xgbr(sample)

Fitting 2 folds for each of 1296 candidates, totalling 2592 fits


## Automated Feature Engineering Strategies (Optional)

As we saw from the last section feature engineering requires a decent understanding of the data, because you'll need to understand what size are reasonable for the coefficients, but also you'll need to understand why t-tests pass or fail.  If you have that understanding of the data and the magnitudes of the various coefficients then you will always be able to build a stronger statistical model by making use of manual feature engineering.

That said manual feature engineering isn't always the best strategy for feature engineering.  It very much depends on the data.  If the data has features that aren't intuitive to a human then it's likely an automated feature engineering strategy will be superior.

Examples of types of data when automated strategies will do better include:

* dealing with text processing
* dealing with image processing
* dealing with video processing

The reason automated feature engineering tends to do better here should be obvious - the features generated from the data don't make sense to a human the same way that the data we've been dealing with thus far does.

## Specific Strategies

* Feature Ranking
* Recursive Feature Engineering


In [ ]:
from skfeature.function.statistical_based import chi_square
from skfeature.function.information_theoretical_based import CIFE
from skfeature.function.statistical_based import CFS
from skfeature.function.information_theoretical_based import CMIM
from skfeature.function.information_theoretical_based import DISR
from skfeature.function.information_theoretical_based import FCBF
from skfeature.function.information_theoretical_based import ICAP
from skfeature.function.information_theoretical_based import JMI
from skfeature.function.information_theoretical_based import MIFS
from skfeature.function.information_theoretical_based import MIM
from skfeature.function.information_theoretical_based import MRMR
from skfeature.function.similarity_based import SPEC

def feature_selection_automation(sample):
    map_values = {
        False: 0,
        True: 1
    }
    y = sample["tip_percentage"] != 0
    y = y.map(map_values)
    columns = sample.columns.tolist()
    columns.remove("tip_percentage")
    X = sample[columns]
    
    features_per_algorithm = {}
    score = chi_square.chi_square(X, y)
    chi_idx = chi_square.feature_ranking(score)
    features_per_algorithm["chi"] = [columns[index] 
                                     for index in chi_idx[0:8]]
    cfs_idx = CFS.cfs(X.as_matrix(), y.as_matrix())
    features_per_algorithm["cfs"] = [columns[index] 
                                     for index in cfs_idx[0:8]]
    cife_idx = CIFE.cife(X.as_matrix(), y.as_matrix())
    features_per_algorithm["cife"] = [columns[index] 
                                     for index in cife_idx[0:8]]
    cmim_idx = CMIM.cmim(X.as_matrix(), y.as_matrix())
    features_per_algorithm["cmim"] = [columns[index] 
                                     for index in cmim_idx[0:8]]
    disr_idx = DISR.disr(X.as_matrix(), y.as_matrix(),
                         n_selected_features=8)
    features_per_algorithm["disr"] = [columns[index] 
                                     for index in disr_idx[0:8]]
    fcbf_idx = FCBF.fcbf(X.as_matrix(), y.as_matrix(),
                         n_selected_features=8)
    features_per_algorithm["fcbf"] = [columns[index] 
                                     for index in fcbf_idx[0:8]]
    icap_idx = ICAP.icap(X.as_matrix(), y.as_matrix(),
                         n_selected_features=8)
    features_per_algorithm["icap"] = [columns[index] 
                                     for index in icap_idx[0:8]]
    jmi_idx = JMI.jmi(X.as_matrix(), y.as_matrix(),
                         n_selected_features=8)
    features_per_algorithm["jmi"] = [columns[index] 
                                     for index in jmi_idx[0:8]]
    mifs_idx = MIFS.mifs(X.as_matrix(), y.as_matrix(),
                         n_selected_features=8)
    features_per_algorithm["mifs"] = [columns[index] 
                                     for index in mifs_idx[0:8]]
    mim_idx = MIM.mim(X.as_matrix(), y.as_matrix(),
                         n_selected_features=8)
    features_per_algorithm["mim"] = [columns[index] 
                                     for index in mim_idx[0:8]]
    mrmr_idx = MRMR.mrmr(X.as_matrix(), y.as_matrix(),
                         n_selected_features=8)
    features_per_algorithm["mrmr"] = [columns[index] 
                                     for index in mrmr_idx[0:8]]   
    features_across_all_algorithms = []
    for column in columns:
        tmp = []
        for algo in features_per_algorithm:
            tmp.append(column in features_per_algorithm[algo])
        if all(tmp):
            features_across_all_algorithms.append(column)
    return features_per_algorithm, features_across_all_algorithms

cols = sample.columns.tolist()
cols.remove("VendorID")
cols.remove("lpep_pickup_datetime")
cols.remove("Lpep_dropoff_datetime")
cols.remove("Store_and_fwd_flag")
cols.remove("RateCodeID")
cols.remove("Pickup_longitude")
cols.remove("Pickup_latitude")
cols.remove("Dropoff_longitude")
cols.remove("Dropoff_latitude")
subsample = sample[cols]
subsample = subsample.replace([np.inf, -np.inf], np.nan)
subsample = subsample[pd.notnull(subsample["ave_speed"])]
features_per_algorithm, features_across_all = feature_selection_automation(subsample)